In [7]:
%run ../code/init_mooc_nb.ipy

from matplotlib import cm
from ipywidgets import RadioWidget
import scipy

class SimpleNamespace(object):
    def __init__(self, **kwargs):
        self.__dict__.update(kwargs)


Performing the necessary imports.

from __future__ import division, print_function
import numpy as np
import matplotlib
import kwant

import ipywidgets
from IPython.html.widgets import interact
from ipywidgets import StaticInteract, RangeWidget, DropDownWidget
from IPython.display import display_html
from matplotlib import pyplot as plt

import pfaffian as pf
from edx_components import *



:0: FutureWarning: IPython widgets are experimental and may change in the future.


Press this button to show/hide the code used in the notebook:

##System 

Let the original square lattice has lattice constant $1$ and $\mathbf{a}=(0,1)$, $\mathbf{b}=(1,0)$ are the directions where the lattice has translational symmetry
$\mathbf{c_1}=(\sqrt{2},\sqrt{2})$ and  $\mathbf{c_2}=(-\sqrt{2},\sqrt{2})$ are the two diagonal vectors.
Let us break the sqaure lattice into two sublattices, each is a square lattice with lattice constant $\sqrt{2}$. Now we condiser a site denoted by creatoin operator $c^\dagger$, it is coupled to the site above and below it by $t$, and the site to the right $-it a^\dagger b $, the sight to the left $it a^\dagger b$. The Bloch Hamiltonian therefore looks like
$$
H_0(\mathbf{k})= \begin{pmatrix} 0 & h(\mathbf{k}) \\ h^\dagger(\mathbf{k}) & 0 \end{pmatrix}\,,
$$

with $\mathbf{k}=(k_x, k_y)$ and

$$h(\mathbf{k}) = t\exp\,\left(i\,\mathbf{k}\cdot\mathbf{a}\right)\,+t\exp\,\left(-i\,\mathbf{k}\cdot\mathbf{a}\right)\,
+ it\exp\,\left(i\,\mathbf{k}\cdot\mathbf{b}\right)\,-it\exp\,\left(-i\,\mathbf{k}\cdot\mathbf{b}\right)\,\\
=2ti cos(\mathbf{k}\mathbf{a})+2t sin(\mathbf{k}\mathbf{b})\\
=2ti cos(k_y)+2t sin(k_x)
.$$

We can see that $h(\mathbf{k})$ becomes $0$ when $k_x=0,\pi$ and $k_y=\pm \pi/2$.

We can see from $H_0$ that when $t_d$ is $0$, the system has dirac points at $k_x=0,\pi$ and $k_y=\pm \pi/2$. (Does it mean there are $4$ Dirac points?) 

I tried introducing nearest neighbor hopping $t_d$ to one sublattice and $-t_d$ to another sublattice. The direction of the interactions are $(1,1)$ and $(-1,1)$. Now the Hamiltonian looks like
$$
H(\mathbf{k})=H_0(\mathbf{k})+\sigma_z 2t_d [cos(k_x+k_y)+cos(k_x-k_y))]\\
=-2tcos(k_y)\sigma_y+2tsin(k_x)\sigma_x+\sigma_z 2t_d [cos(k_x+k_y)+cos(k_x-k_y))]
$$
We can see from the interactive figure below that when $t_d=0$, the gap closes at $k_x=0$ and $k_x=\pm \pi$, which matches our observation from $H_0$. 

In [2]:

#Finite system
def Qi_Wu_Zhang_ribbon(w):
    sigma_x = np.array([[0, 1], [1, 0]])
    sigma_y = np.array([[0, -1j], [1j, 0]])
    sigma_z = np.array([[1, 0], [0, -1]])
    
    def ribbon_shape(pos):
        (x, y) = pos
        return (0 <= y < w )
    
    def onsite(site, par):
        return  0
       #- par.mu * sigma_z
    
    def hopx(target, source, par):
        (x,y)=target.pos
        return  1j * par.t *(-1)**y 
    
    def hopy(target, source, par):    
        return  par.t 
    
    def hopd1(target, source, par):#hopping in the (1,1) direction
        (x,y)=source.pos
        return  par.td*(-1)**(x+y)
    
    def hopd2(target, source, par):
        (x,y)=source.pos
        return  par.td*(-1)**(x+y)
    
    lat = kwant.lattice.square()
    sym = kwant.TranslationalSymmetry((1, 0))
    sys = kwant.Builder(sym)
    
    sys[lat.shape(ribbon_shape, (0, 0))] = onsite
    sys[kwant.HoppingKind((1,0), lat)] = hopx
    sys[kwant.HoppingKind((0,1), lat)] = hopy
    sys[kwant.HoppingKind((1,1), lat)] = hopd1
    sys[kwant.HoppingKind((-1,1), lat)] = hopd2
    return sys.finalized()

par = SimpleNamespace(t=1.0, td=1.0,kx=0.0, ky=0.0)
sys = Qi_Wu_Zhang_ribbon(30)
def Qi_Wu_Zhang_edge_dispersion(td):
    par.td = td
    fig = kwant.plotter.bands(sys, args=[par,], show=False)
    
    plt.xlabel('$k_x$')
    plt.ylabel('$E$')
    plt.ylim([-5, 5])
    plt.xlim(-np.pi, np.pi)
    plt.suptitle('$t = %1.1f,$ $ ,$ $td= %1.1f$' %(par.t, par.td))
    return fig

StaticInteract(lambda td: Qi_Wu_Zhang_edge_dispersion(- 2 + 0.2*td), td=RangeWidget(0, 20))


##Berry Curvature
Unfortunately, I couldn't get the Berry curvature running correctly. 


In [4]:
#returns a kwant system, that resembles the momentum subblock of the Hamiltonian
def make_infinite():
    sigma_x = np.array([[0, 1], [1, 0]])
    sigma_y = np.array([[0, -1j], [1j, 0]])
    sigma_z = np.array([[1, 0], [0, -1]])
    onsite = lambda site, par: (2*par.t * np.sin(par.kx)  * sigma_x  
                                - 2*par.t * np.cos(par.ky) * sigma_y +
                                2 * par.td *(np.cos(par.kx+par.ky) +np.cos(par.kx-par.ky))*sigma_z)

    lat = kwant.lattice.chain()
    sys = kwant.Builder()
    sys[lat(0)] = onsite
    return sys.finalized()
 

In [5]:
def berry_curvature(eigen, num_points=51, num_filled_bands=1):
    K = np.linspace(-np.pi, np.pi, num_points, endpoint=False)

    vectors = np.array([[eigen(kx, ky)[:, :num_filled_bands] for kx in K] for ky in K])

    vectors_x = np.roll(vectors, 1, 0)
    vectors_xy = np.roll(vectors_x, 1, 1)
    vectors_y = np.roll(vectors, 1, 1)

    shifted_vecs = [vectors, vectors_x, vectors_xy, vectors_y]

    v_shape = vectors.shape

    shifted_vecs = [i.reshape(-1, v_shape[-2], v_shape[-1]) for i in shifted_vecs]

    dets = np.ones(len(shifted_vecs[0]), dtype=complex)
    for vec, shifted in zip(shifted_vecs, np.roll(shifted_vecs, 1, 0)):
        dets *= [np.linalg.det(a.T.conj().dot(b)) for a, b in zip(vec, shifted)]
    bc = np.angle(dets).reshape(int(np.sqrt(len(dets))), -1)    
    
    bc = (bc + np.pi/2) % (np.pi) - np.pi/2
    
    return bc
def plot_bc(td):
    par = SimpleNamespace(t=1,td=td, kx=0.0, ky=0.0)
    sys = make_infinite()

    bc = berry_curvature(eigen_func(sys, par), num_points=100)
    vmax = np.max(abs(bc[1:-1][:,1:-1]))  # Discard boundaries due to artifacts.
    
    limit = max(abs(np.min(bc)), abs(np.max(bc)))
    
    fig = plt.figure(figsize=(4,4))
    ax = fig.add_subplot(1, 1, 1)
    ax.imshow(bc, vmin=-vmax, vmax=vmax, origin='lower',
           extent=[-np.pi, np.pi, -np.pi, np.pi], cmap=cm.RdBu_r)

    ax.set_xlabel('$k_x$')
    ax.set_xticks([-np.pi, 0.0, np.pi])
    ax.set_xticklabels(['$-\pi$', '$0$', '$\pi$'])
    ax.set_ylabel('$k_y$')
    ax.set_yticks([-np.pi, 0.0, np.pi])
    ax.set_yticklabels(['$-\pi$', '$0$', '$\pi$'])
    fig.suptitle('$t = %1.1f,$ ' %(par.t));
    return fig

In [13]:
StaticInteract(lambda td: plot_bc(td), td=(-1, 1, 0.1))

AttributeError: 'tuple' object has no attribute 'renamed'